In [ ]:
# ..... Knight-Schrijver et al data ..... #
# integrated fetal + adult HCA data - 60k cells
# using only F1, F2 since this is earliest dev timepoint with
# IVS-human heart - close to last stage in our datasets

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)
library(dplyr)

In [3]:
# subset to fetal 30k cells only
sch = readRDS('knight_fetal_adult_human_heart.rds')
sch <- sch[,(sch$cell_states=='foetal')]
sch <- sch[,sch$age.order %in% c('F1', 'F2')]
sch

An object of class Seurat 
27473 features across 7322 samples within 1 assay 
Active assay: RNA (27473 features, 0 variable features)
 2 layers present: counts, data
 1 dimensional reduction calculated: umap

In [4]:
sch@meta.data[1,]

nCount_RNA nFeature_RNA age_group cell_source cell_states
CATTGTTGTTCCGCGA-C8 5306       2065         NA        F - Base    foetal     
                    sample age.order age.days.GA size.CRL size.NRL ⋯
CATTGTTGTTCCGCGA-C8 C8     F1        58          NA       NA       ⋯
                    suspension_type is_primary_data cell_type  assay    
CATTGTTGTTCCGCGA-C8 cell            TRUE            fibroblast 10x 3' v3
                    disease organism     sex    tissue             
CATTGTTGTTCCGCGA-C8 normal  Homo sapiens female basal zone of heart
                    self_reported_ethnicity
CATTGTTGTTCCGCGA-C8 unknown                
                    development_stage                      
CATTGTTGTTCCGCGA-C8 9th week post-fertilization human stage

In [14]:
unique(as.character(sch$development_stage[as.character(sch$age.order)=='F1']))
unique(as.character(sch$development_stage[as.character(sch$age.order)=='F2']))

[1] "9th week post-fertilization human stage"

[1] "9th week post-fertilization human stage"

In [16]:
# table(sch$clusters.res.2[sch$age.order=='F2'])
table(sch$clusters.res.2)


              Adipocytes           Cardiomyocytes              Endocardial 
                       0                      980                      575 
    Endothelial_Arterial  Endothelial_Capillaries        Endothelial_Other 
                      88                      272                      275 
      Endothelial_Venous       Epicardium_FB-like          Epicardium_Meso 
                      43                       10                       69 
Epicardium_Proliferating              Fibroblasts  Immature_Cardiomyocytes 
                       4                     1413                      487 
          Immature_other    Lymphoid_Immune_Cells     Myeloid_Immune_Cells 
                    1398                       83                      778 
          Neuronal_Cells                Pericytes        Pericytes_Stromal 
                     132                      323                        0 
     Smooth_Muscle_Cells 
                     392 

In [17]:
# cell types in clusters.low.res, clusters.res.2, clusters.res.3
c1 = unique(sch$clusters.res.2)
c1
length(c1)

[1] Fibroblasts              Smooth_Muscle_Cells      Pericytes               
 [4] Immature_other           Endocardial              Endothelial_Venous      
 [7] Endothelial_Arterial     Endothelial_Other        Endothelial_Capillaries 
[10] Cardiomyocytes           Immature_Cardiomyocytes  Myeloid_Immune_Cells    
[13] Neuronal_Cells           Epicardium_Meso          Epicardium_FB-like      
[16] Lymphoid_Immune_Cells    Epicardium_Proliferating
19 Levels: Adipocytes Cardiomyocytes Endocardial ... Smooth_Muscle_Cells

[1] 17

In [18]:
table(sch$clusters.res.3)


                Adipocytes      Atrial_Cardiomyocytes 
                         0                        144 
                   B_cells            Dendritic_Cells 
                         7                          1 
               Endocardial       Endothelial_Arterial 
                       575                         88 
   Endothelial_Capillaries          Endothelial_Other 
                       272                        275 
        Endothelial_Venous         Epicardium_FB-like 
                        43                         10 
           Epicardium_Meso   Epicardium_Proliferating 
                        69                          4 
           Fibroblast-like                Fibroblasts 
                       908                        505 
   Immature_Cardiomyocytes       Immature_Endothelium 
                      1161                        577 
          Immature_FB-like       Immature_Neuralcrest 
                       546                          8 
         

In [19]:
# get SCE object
sce2 = SingleCellExperiment(list(counts = GetAssayData(sch, 'counts')),
                            colData = DataFrame(sch@meta.data))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))

In [24]:
# get cell type markers on foetal data
markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$clusters.res.2)
# markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$clusters.res.3, 
#                           group_labels = sce2$clusters.res.2)
head(markers)

group cell_type      gene            fold_change auroc     log_fdr   
1 all   Cardiomyocytes ENSG00000155657 19.985762   0.9787084 -1158.7044
2 all   Cardiomyocytes ENSG00000118194 10.775696   0.9672153 -1104.0121
3 all   Cardiomyocytes ENSG00000106631  8.707820   0.9540668 -1042.9912
4 all   Cardiomyocytes ENSG00000159251  9.827920   0.9525591 -1036.2500
5 all   Cardiomyocytes ENSG00000198336  8.179446   0.9434210  -995.1240
6 all   Cardiomyocytes ENSG00000183023 13.783580   0.9405897  -982.6597
  population_size population_fraction average_expression se_expression
1 980             0.1338432            4336.561          100.06911    
2 980             0.1338432            6206.563           79.37330    
3 980             0.1338432           18725.667          360.11779    
4 980             0.1338432            9660.593          197.44516    
5 980             0.1338432            4964.836           88.11112    
6 980             0.1338432            1110.734           33.28189    
  detection_rate fold_change_detection precision recall   
1 0.9928571      3.540355              0.3542046 0.9928571
2 0.9948980      2.202732              0.2541710 0.9948980
3 1.0000000      1.495014              0.1877395 1.0000000
4 0.9908163      1.796996              0.2174692 0.9908163
5 0.9867347      2.212454              0.2550105 0.9867347
6 0.9530612      4.030165              0.3845204 0.9530612

In [21]:
# convert gene names to symbols
ginfo = read.delim('/data/CoCoCoNet/geneInfo/human_info.csv', sep = ',')
ginfo[1,]

EntrezID  EnsemblID       GeneSymbol LocusTag Synonyms
1 100287102 ENSG00000223972 DDX11L1    NA       NA      
  dbXrefs                                   Chromosome Type   UniProtID
1 |HGNC:HGNC:37102|Ensembl:ENSG00000223972| 1          pseudo NA       
  UniProtID2 OrthoID NetworkIDs     
1 NA         NA      ENSG00000223972

In [25]:
# remove genes w/o symbols
markers$gene <- ginfo$GeneSymbol[match(markers$gene, ginfo$EnsemblID)]
dim(markers)
markers <- markers[!is.na(markers$gene),]
dim(markers)

[1] 467041     14

[1] 351900     14

In [35]:
head(markers[markers$cell_type=='Fibroblasts',])
head(markers[markers$cell_type=='Cardiomyocytes',])

group       cell_type   gene     fold_change auroc     log_fdr  
1 Fibroblasts Fibroblasts SCN7A    7.536470    0.7657756 -434.1200
2 Fibroblasts Fibroblasts DCN      2.697889    0.7638538 -428.0657
3 Fibroblasts Fibroblasts TCF21    3.543116    0.7425419 -361.2187
4 Fibroblasts Fibroblasts COLEC11  8.126321    0.7153363 -284.0825
5 Fibroblasts Fibroblasts TMSB4X   1.947135    0.7110391 -272.8414
6 Fibroblasts Fibroblasts SERPINE2 3.246704    0.7067351 -261.8529
  population_size population_fraction average_expression se_expression
1 1859            0.4418826            534.5375          17.034346    
2 1859            0.4418826           2140.8305          45.839618    
3 1859            0.4418826            654.5267          14.688772    
4 1859            0.4418826            255.8069           8.626622    
5 1859            0.4418826           4359.4479          74.739818    
6 1859            0.4418826            703.8845          19.642739    
  detection_rate fold_change_detection precision recall   
1 0.6401291      4.3338989             0.7752443 0.6401291
2 0.8423884      1.7289731             0.5780731 0.8423884
3 0.7315761      1.7986013             0.5877269 0.7315761
4 0.5185584      4.5124175             0.7824675 0.5185584
5 0.9494352      0.9726606             0.4350505 0.9494352
6 0.6966111      1.5418590             0.5498938 0.6966111

group cell_type gene fold_change auroc log_fdr population_size
     population_fraction average_expression se_expression detection_rate
     fold_change_detection precision recall

In [26]:
# save marker list
export_meta_markers(markers, "Knight-Schrijver_celltype_markers_F1_F2_res2.csv", names(markers))
# export_meta_markers(markers, "Knight-Schrijver_celltype_markers_F1_F2_res3.csv", names(markers))